## References
- [Written Memories: Understanding, Deriving and Extending the LSTM](https://r2rt.com/written-memories-understanding-deriving-and-extending-the-lstm.html)
- [Recurrent Neural Networks in Tensorflow 1](https://r2rt.com/recurrent-neural-networks-in-tensorflow-i.html)
- [Recurrent Neural Networks Tutorial](http://www.wildml.com/2015/09/recurrent-neural-networks-tutorial-part-1-introduction-to-rnns/)

- [RNNs in Tensorflow, a Practical Guide and Undocumented Features](http://www.wildml.com/2016/08/rnns-in-tensorflow-a-practical-guide-and-undocumented-features/)


# Implementing RNN from scratch
This part is essentially the reproduction of [Recurrent Neural Networks in Tensorflow 1](http://www.wildml.com/2015/09/recurrent-neural-networks-tutorial-part-2-implementing-a-language-model-rnn-with-python-numpy-and-theano/)

## 1. Constructing the Input for RNN

In [1]:
# Read the corpus file
import re
with open('wiki.dl.history.txt') as f:
    corpus = re.sub('\[[0-9]*\]','',f.read()).lower() # preprocessing
print(corpus[:1000])

# Build the Vocabulary
from collections import Counter
from nltk import word_tokenize

vocab_size = 300 # size of the vocabulary
corpus_tokenized = word_tokenize(corpus)
counter = Counter(corpus_tokenized)
# Special Characters
_UNKNOWN_ = '_UNKNOWN_' # unknown tokens
_BEGIN_ = '_BEGIN_' # beginning of the sentence
_END_ = '_END_' # end of the sentence
vocab = [word for word,cnt in counter.most_common(vocab_size - 3)] + [_UNKNOWN_,_BEGIN_,_END_]

print('The total number of words in the corpus: %i' % len(counter.most_common()))
print('The size of the vocabulary(including _UNKNOWN_,_BEGIN_,_END_): %i' % vocab_size)

# Define the mapping between word <-> id
word2id = {w: i for i, w in enumerate(vocab)}
id2word = {i: w for i, w in enumerate(vocab)}

# tokenize the corpus into sentences
from nltk import sent_tokenize
sentences = ['%s %s %s' % (_BEGIN_,sent,_END_) for sent in sent_tokenize(corpus)]
sentences_tokenized = [word_tokenize(sent) for sent in sentences]
for i,sent in enumerate(sentences_tokenized):
    sentences_tokenized[i] = [word if word in vocab else _UNKNOWN_ for word in sent]
print(sentences_tokenized[:5],'\n')

# Map the words in the sentences into ID's
X_train = [[word2id[word] for word in sent[:-1]] for sent in sentences_tokenized]
Y_train = [[word2id[word] for word in sent[1:]] for sent in sentences_tokenized]
# Example Training set
print(X_train[0])
print(' '.join([id2word[i] for i in X_train[0]]))
print(Y_train[0])
print(' '.join([id2word[i] for i in Y_train[0]]))

sentences2id = [[word2id[word] for word in sent] for sent in sentences_tokenized]

def gen_seq(sentences2id,sequence_length=5):
    '''
    Converts the sentences into training sequences
    Corresponds to the batch size of 1
    '''
    for sent in sentences2id:
        for i in range(len(sent)-sequence_length):
            x_batch = sent[i:i+sequence_length]
            y_batch = sent[i+1:i+sequence_length+1]
            yield x_batch,y_batch
            
dataX = []
dataY = []
for x,y in gen_seq(sentences2id[:200]):
    dataX.append(x)
    dataY.append(y)

according to a survey, the expression deep learning was introduced to the machine learning community by rina dechter in 1986, and later to artificial neural networks by igor aizenberg and colleagues in 2000, in the context of boolean threshold neurons. in 2005, faustino gomez and jürgen schmidhuber published a paper on learning deep pomdps through neural networks for reinforcement learning. in 2006, a publication by hinton, osindero, and teh drew attention by showing how many-layered feedforward neural network could be effectively pre-trained one layer at a time, treating each layer in turn as an unsupervised restricted boltzmann machine, then fine-tuning it using supervised backpropagation. the paper referred to learning for deep belief nets. a google ngram chart shows that the usage of the term has taken off since 2000. the underlying concepts and many techniques, however, date to earlier decades.

the first general, working learning algorithm for supervised, deep, feedforward, multi

The LSTM model with an FC layer works quite well.

In [2]:
# Baseline(using tensorflow.contrib)
import tensorflow as tf
import numpy as np
from tensorflow.contrib import rnn
tf.set_random_seed(123)

# Global hyperparameters for comparing models
hidden_size = 200
sequence_length = 5  # Any arbitrary number
learning_rate = 0.1
n_epochs = 3000
batch_size = len(dataX)

## 2. RNN Implementation

Below is the hard-coded version of simple RNN using only the basic functions of tensorflow.  
The notations for the variables follow [here](http://www.wildml.com/2015/09/recurrent-neural-networks-tutorial-part-1-introduction-to-rnns/)
![image.png](http://d3kbpzbmcynnmx.cloudfront.net/wp-content/uploads/2015/09/rnn.jpg)
It turns out that the RNNs of this simple structure(no bias / no FC layers) takes some time to learn a complicated structure.

In [3]:
tf.reset_default_graph()
tf.set_random_seed(123)

class Model():
    '''
    vanilla RNN from scratch
    '''
    def __init__(self):
        # attach a session to tensorflow
        self.sess = tf.Session()
        self.build_graph()
        self.sess.run(tf.global_variables_initializer())
        
    def build_graph(self):
        
        # Declare the variables for the RNN cell
        with tf.variable_scope('rnn_cell'):
            U = tf.get_variable('U',(vocab_size,hidden_size),dtype=tf.float32)
            W = tf.get_variable('W',(hidden_size,hidden_size),dtype=tf.float32)
        
        # Declare the variable for the softmax layer
        V = tf.get_variable('V',(hidden_size,vocab_size),dtype=tf.float32)
             
        # Step 1: construct the inputs
        self.x = tf.placeholder(tf.int32, (batch_size, sequence_length))
        self.y = tf.placeholder(tf.int32, (batch_size, sequence_length))
        x_one_hot = tf.one_hot(self.x, vocab_size)
        # construct the words in a single sentence as a 
        # list of individual training instances
        x_list = tf.unstack(x_one_hot, axis = 1)
        
        # Step 2: Calculate the states for each time step
        # initialize the state to zeros(s_0)
        state = tf.zeros((batch_size, hidden_size))
        self.states = []
        for x_t in x_list:
            state = self.rnn_cell(x_t, state)
            self.states.append(state)
        
        # Step 3: Calculate the losses
        logits = [tf.matmul(state,V) for state in self.states]
        self.predictions = [tf.nn.softmax(logit) for logit in logits]
        # labels: Tensor with each entry in [0,num_classes)
        # refer to: https://stackoverflow.com/questions/37312421/tensorflow-whats-the-difference-between-sparse-softmax-cross-entropy-with-logi
        labels = tf.unstack(self.y, axis = 1)
        losses = [tf.nn.sparse_softmax_cross_entropy_with_logits(
        logits = logits, labels = labels)]
        self.cost = tf.reduce_mean(losses) # average cross-entropy loss
        self.optimizer =\
        tf.train.AdagradOptimizer(learning_rate).minimize(self.cost)
    
    def rnn_cell(self, x_t, state_prev):
        ''' 
        Calculates the next state, given x_t(the current input)
        and the previous state
        
        Args:
            x_t: 
            state_prev: previous state of the hidden layer
            
        Returns:
            state_current: current state of the hidden layer
        '''
        with tf.variable_scope('rnn_cell', reuse=True):
            U = tf.get_variable('U',(vocab_size,
                                     hidden_size))
            W = tf.get_variable('W',(hidden_size,
                                     hidden_size))
        state_current = tf.tanh(tf.matmul(x_t, U) + \
                        tf.matmul(state_prev, W))
        return state_current
            
    def train(self, x, y):
        return self.sess.run([self.cost,
                              self.optimizer,
                              self.predictions],
                            feed_dict={self.x:x,self.y:y})
m = Model()

print('Learning Started')

for epoch in range(n_epochs):
    c, _, pred = m.train(dataX, dataY)
    print('Epoch:%04d' %(epoch+1),'cost:%.9f' % c)
    if epoch % 100 == 0:
        # predict the words using the softmax value
        for j,batch in enumerate(np.argmax(np.array(pred),axis=2).T):
            words = ' '.join([id2word[i] for i in batch])
            print(epoch,j,words)

print('Learning Finished')

Learning Started
Epoch:0001 cost:5.708302498
0 0 ivakhnenko research taken has mixture
0 1 chart late has architectures cnns
0 2 late survey network cnns that
0 3 two architectures cnns units turn
0 4 lstm alpha demonstrated turn are
0 5 were while artificial 8 lstm
0 6 weng artificial 8 late demonstrated
0 7 turn 1990s also demonstrated many-layered
0 8 while combined involved automatic other
0 9 demonstrated usage many-layered off has
0 10 directly and off such big
0 11 identification hinton such big weng
0 12 late ” 3-d neocognitron cascade
0 13 weng neurons handling cascade cascade
0 14 for ( be it ”
0 15 demonstrated involved models colleagues learning
0 16 time models deep learning those
0 17 than [ 2006 those 1986
0 18 artificial learning workshop 1986 network
0 19 time those 1986 have dnns
0 20 into turn can learned that
0 21 feature deng these as implemented
0 22 were neocognitron that off can
0 23 these began neural many 3-d
0 24 began neural speech 3-d 2006
0 25 late many 3-

0 1094 weng results cluttered handcrafted general
0 1095 1986 usage rnns general demonstrated
0 1096 directly handcrafted than demonstrated fine-tuning
0 1097 experienced than then fine-tuning since
0 1098 than weng handcrafted since general
0 1099 weng handcrafted 1991 cascade than
0 1100 experienced graphics 1970 recurrent dechter
0 1101 since working hardware % 1991
0 1102 while hinton as 1991 belief
0 1103 hinton % 3-d model were
0 1104 hand-written efficient belief other neocognitron
0 1105 since nets were implemented nvidia
0 1106 belief were neocognitron nvidia referred
0 1107 were neocognitron research rina than
0 1108 these research differentiation graphics demonstrated
0 1109 weng handcrafted directly 3-d started
0 1110 experienced recurrent then experienced us
0 1111 recurrent hinton experienced zip osindero
0 1112 weng handcrafted trained cascade algorithm
0 1113 experienced trained cascade ” are
0 1114 were algorithm a efficient neocognitron
0 1115 experienced boolean micr

Epoch:0024 cost:5.267600536
Epoch:0025 cost:5.250553131
Epoch:0026 cost:5.233145237
Epoch:0027 cost:5.215379238
Epoch:0028 cost:5.197271824
Epoch:0029 cost:5.178860664
Epoch:0030 cost:5.160206318
Epoch:0031 cost:5.141394615
Epoch:0032 cost:5.122542381
Epoch:0033 cost:5.103789806
Epoch:0034 cost:5.085292339
Epoch:0035 cost:5.067204952
Epoch:0036 cost:5.049664497
Epoch:0037 cost:5.032765865
Epoch:0038 cost:5.016561985
Epoch:0039 cost:5.001060963
Epoch:0040 cost:4.986240864
Epoch:0041 cost:4.972068787
Epoch:0042 cost:4.958508492
Epoch:0043 cost:4.945533276
Epoch:0044 cost:4.933121204
Epoch:0045 cost:4.921257973
Epoch:0046 cost:4.909933090
Epoch:0047 cost:4.899136543
Epoch:0048 cost:4.888858318
Epoch:0049 cost:4.879085064
Epoch:0050 cost:4.869796753
Epoch:0051 cost:4.860970974
Epoch:0052 cost:4.852579117
Epoch:0053 cost:4.844589233
Epoch:0054 cost:4.836967468
Epoch:0055 cost:4.829678535
Epoch:0056 cost:4.822687626
Epoch:0057 cost:4.815962791
Epoch:0058 cost:4.809474468
Epoch:0059 cost:4.80

100 649 _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ .
100 650 _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ .
100 651 _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ . _END_
100 652 have _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ the
100 653 _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ the .
100 654 _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ .
100 655 layer _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_
100 656 _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_
100 657 technology _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_
100 658 _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_
100 659 _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_
100 660 _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ .
100 661 _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_
100 662 _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_
100 663 _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_
100 664 , _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_
100 665 _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ .
100 666 _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ . .
100 667 _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ . _UNKNOWN_
100 668 _U

Epoch:0113 cost:4.619836807
Epoch:0114 cost:4.603267670
Epoch:0115 cost:4.612789154
Epoch:0116 cost:4.596904755
Epoch:0117 cost:4.605959892
Epoch:0118 cost:4.590652466
Epoch:0119 cost:4.599312305
Epoch:0120 cost:4.584496021
Epoch:0121 cost:4.592816830
Epoch:0122 cost:4.578424454
Epoch:0123 cost:4.586448669
Epoch:0124 cost:4.572426796
Epoch:0125 cost:4.580187321
Epoch:0126 cost:4.566494942
Epoch:0127 cost:4.574017048
Epoch:0128 cost:4.560619354
Epoch:0129 cost:4.567924500
Epoch:0130 cost:4.554794312
Epoch:0131 cost:4.561899185
Epoch:0132 cost:4.549015045
Epoch:0133 cost:4.555932999
Epoch:0134 cost:4.543275356
Epoch:0135 cost:4.550018311
Epoch:0136 cost:4.537570953
Epoch:0137 cost:4.544149399
Epoch:0138 cost:4.531898499
Epoch:0139 cost:4.538320541
Epoch:0140 cost:4.526254654
Epoch:0141 cost:4.532528400
Epoch:0142 cost:4.520635128
Epoch:0143 cost:4.526768684
Epoch:0144 cost:4.515037060
Epoch:0145 cost:4.521036625
Epoch:0146 cost:4.509459496
Epoch:0147 cost:4.515330315
Epoch:0148 cost:4.50

...

Epoch:2719 cost:0.945258081
Epoch:2720 cost:0.945913672
Epoch:2721 cost:0.944855332
Epoch:2722 cost:0.945505023
Epoch:2723 cost:0.944452882
Epoch:2724 cost:0.945098221
Epoch:2725 cost:0.944053590
Epoch:2726 cost:0.944696367
Epoch:2727 cost:0.943660200
Epoch:2728 cost:0.944301963
Epoch:2729 cost:0.943274617
Epoch:2730 cost:0.943916500
Epoch:2731 cost:0.942898035
Epoch:2732 cost:0.943540454
Epoch:2733 cost:0.942530274
Epoch:2734 cost:0.943172634
Epoch:2735 cost:0.942169547
Epoch:2736 cost:0.942811012
Epoch:2737 cost:0.941813350
Epoch:2738 cost:0.942452550
Epoch:2739 cost:0.941458464
Epoch:2740 cost:0.942093670
Epoch:2741 cost:0.941101432
Epoch:2742 cost:0.941731095
Epoch:2743 cost:0.940739453
Epoch:2744 cost:0.941361904
Epoch:2745 cost:0.940370202
Epoch:2746 cost:0.940984488
Epoch:2747 cost:0.939992547
Epoch:2748 cost:0.940598249
Epoch:2749 cost:0.939606547
Epoch:2750 cost:0.940203071
Epoch:2751 cost:0.939212978
Epoch:2752 cost:0.939800382
Epoch:2753 cost:0.938812852
Epoch:2754 cost:0.93

2800 678 _UNKNOWN_ the _UNKNOWN_ 1990s .
2800 679 _UNKNOWN_ _UNKNOWN_ 1990s . _END_
2800 680 _UNKNOWN_ _UNKNOWN_ the us _UNKNOWN_
2800 681 _UNKNOWN_ a _UNKNOWN_ _UNKNOWN_ 's
2800 682 a _UNKNOWN_ _UNKNOWN_ 's _UNKNOWN_
2800 683 _UNKNOWN_ _UNKNOWN_ 's _UNKNOWN_ and
2800 684 _UNKNOWN_ 's _UNKNOWN_ and _UNKNOWN_
2800 685 _UNKNOWN_ _UNKNOWN_ and _UNKNOWN_ ,
2800 686 _UNKNOWN_ and _UNKNOWN_ , sri
2800 687 _UNKNOWN_ _UNKNOWN_ , sri _UNKNOWN_
2800 688 _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ research
2800 689 _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ research on
2800 690 _UNKNOWN_ _UNKNOWN_ research on deep
2800 691 _UNKNOWN_ in on deep neural
2800 692 _UNKNOWN_ on deep neural networks
2800 693 on deep neural networks in
2800 694 deep neural networks in speech
2800 695 learning networks in speech and
2800 696 networks in speech recognition speaker
2800 697 in speech recognition speaker recognition
2800 698 _UNKNOWN_ recognition speaker recognition .
2800 699 recognition speaker recognition . _END_
2800 700

Epoch:2815 cost:0.927553535
Epoch:2816 cost:0.928151250
Epoch:2817 cost:0.927181244
Epoch:2818 cost:0.927773118
Epoch:2819 cost:0.926806331
Epoch:2820 cost:0.927394152
Epoch:2821 cost:0.926430941
Epoch:2822 cost:0.927016556
Epoch:2823 cost:0.926057220
Epoch:2824 cost:0.926643074
Epoch:2825 cost:0.925687790
Epoch:2826 cost:0.926276386
Epoch:2827 cost:0.925325215
Epoch:2828 cost:0.925918639
Epoch:2829 cost:0.924971700
Epoch:2830 cost:0.925571561
Epoch:2831 cost:0.924628615
Epoch:2832 cost:0.925235569
Epoch:2833 cost:0.924296260
Epoch:2834 cost:0.924910307
Epoch:2835 cost:0.923974097
Epoch:2836 cost:0.924593687
Epoch:2837 cost:0.923660040
Epoch:2838 cost:0.924282551
Epoch:2839 cost:0.923350692
Epoch:2840 cost:0.923972905
Epoch:2841 cost:0.923042178
Epoch:2842 cost:0.923660278
Epoch:2843 cost:0.922730088
Epoch:2844 cost:0.923340261
Epoch:2845 cost:0.922410309
Epoch:2846 cost:0.923009396
Epoch:2847 cost:0.922079921
Epoch:2848 cost:0.922665656
Epoch:2849 cost:0.921737075
Epoch:2850 cost:0.92

2900 585 _UNKNOWN_ lack of _UNKNOWN_ of
2900 586 _UNKNOWN_ of _UNKNOWN_ of how
2900 587 of _UNKNOWN_ of how the
2900 588 deep , how the brain
2900 589 _UNKNOWN_ _UNKNOWN_ the brain _UNKNOWN_
2900 590 deep the brain _UNKNOWN_ its
2900 591 the brain _UNKNOWN_ its _UNKNOWN_
2900 592 _UNKNOWN_ _UNKNOWN_ its _UNKNOWN_ networks
2900 593 _UNKNOWN_ its _UNKNOWN_ networks .
2900 594 _UNKNOWN_ _UNKNOWN_ networks . _END_
2900 595 _UNKNOWN_ _UNKNOWN_ and deep learning
2900 596 _UNKNOWN_ _UNKNOWN_ _UNKNOWN_ learning (
2900 597 _UNKNOWN_ _UNKNOWN_ learning ( _UNKNOWN_
2900 598 _UNKNOWN_ learning ( _UNKNOWN_ ,
2900 599 learning to _UNKNOWN_ , recurrent
2900 600 to _UNKNOWN_ , recurrent nets
2900 601 _UNKNOWN_ ) recurrent nets )
2900 602 _UNKNOWN_ _UNKNOWN_ nets ) of
2900 603 _UNKNOWN_ nets ) of anns
2900 604 neural ) of anns have
2900 605 ( of anns have been
2900 606 , _UNKNOWN_ have been _UNKNOWN_
2900 607 deep _UNKNOWN_ been _UNKNOWN_ for
2900 608 _UNKNOWN_ been _UNKNOWN_ for many
2900 609 been _UN

Epoch:2912 cost:0.911813796
Epoch:2913 cost:0.910912633
Epoch:2914 cost:0.911472857
Epoch:2915 cost:0.910574794
Epoch:2916 cost:0.911124885
Epoch:2917 cost:0.910230458
Epoch:2918 cost:0.910770655
Epoch:2919 cost:0.909880221
Epoch:2920 cost:0.910411477
Epoch:2921 cost:0.909525454
Epoch:2922 cost:0.910049558
Epoch:2923 cost:0.909168005
Epoch:2924 cost:0.909687042
Epoch:2925 cost:0.908810139
Epoch:2926 cost:0.909326971
Epoch:2927 cost:0.908454597
Epoch:2928 cost:0.908972204
Epoch:2929 cost:0.908104122
Epoch:2930 cost:0.908625782
Epoch:2931 cost:0.907761574
Epoch:2932 cost:0.908290505
Epoch:2933 cost:0.907429516
Epoch:2934 cost:0.907968104
Epoch:2935 cost:0.907109678
Epoch:2936 cost:0.907659829
Epoch:2937 cost:0.906803071
Epoch:2938 cost:0.907365441
Epoch:2939 cost:0.906509519
Epoch:2940 cost:0.907083333
Epoch:2941 cost:0.906227291
Epoch:2942 cost:0.906810522
Epoch:2943 cost:0.905953646
Epoch:2944 cost:0.906542659
Epoch:2945 cost:0.905684233
Epoch:2946 cost:0.906274498
Epoch:2947 cost:0.90

In [4]:
tf.reset_default_graph()
tf.set_random_seed(123)

class Model():
    '''
    Static RNN using the BasicRNNCell API
    '''
    def __init__(self):
        # attach a session to tensorflow
        self.sess = tf.Session()
        self.build_graph()
        self.sess.run(tf.global_variables_initializer())
        
    def build_graph(self):
        
        # Declare the variable for the softmax layer
        V = tf.get_variable('V',(hidden_size,vocab_size),dtype=tf.float32)
             
        # Step 1: construct the inputs
        self.x = tf.placeholder(tf.int32, (batch_size, sequence_length))
        self.y = tf.placeholder(tf.int32, (batch_size, sequence_length))
        x_one_hot = tf.one_hot(self.x, vocab_size)
        # construct the words in a single sentence as a 
        # list of individual training instances
        x_list = tf.unstack(x_one_hot, axis = 1)
        
        # Step 2: Calculate the states for each time step
        # initialize the state to zeros(s_0)
        rnn_cell = tf.contrib.rnn.BasicRNNCell(hidden_size)
        s0 = tf.zeros((batch_size, hidden_size))
        self.states, _ = tf.contrib.rnn.static_rnn(rnn_cell,
                                                   x_list,
                                                   initial_state=s0)
        
        # Step 3: Calculate the losses
        logits = [tf.matmul(state,V) for state in self.states]
        self.predictions = [tf.nn.softmax(logit) for logit in logits]
        # labels: Tensor with each entry in [0,num_classes)
        # refer to: https://stackoverflow.com/questions/37312421/tensorflow-whats-the-difference-between-sparse-softmax-cross-entropy-with-logi
        labels = tf.unstack(self.y, axis = 1)
        losses = [tf.nn.sparse_softmax_cross_entropy_with_logits(
        logits = logits, labels = labels)]
        self.cost = tf.reduce_mean(losses) # average cross-entropy loss
        self.optimizer =\
        tf.train.AdagradOptimizer(learning_rate).minimize(self.cost)
            
    def train(self, x, y):
        return self.sess.run([self.cost,
                              self.optimizer,
                              self.states],
                            feed_dict={self.x:x,self.y:y})
m = Model()

print('Learning Started')

for epoch in range(n_epochs):
    c, _, pred = m.train(dataX, dataY)
    print('Epoch:%04d' %(epoch+1),'cost:%.9f' % c)
    if epoch % 100 == 0:
        # predict the words using the softmax value
        for j,batch in enumerate(np.argmax(np.array(pred),axis=2).T):
            words = ' '.join([id2word[i] for i in batch])
            print(epoch,j,words)

print('Learning Finished')

Learning Started
Epoch:0001 cost:5.702800274
0 0 survey model model “ since
0 1 time al “ since ”
0 2 and “ since . 1990s
0 3 one since . first learning
0 4 temporal . 1990s learning later
0 5 all similar models later 3-d
0 6 first networks later 3-d neural
0 7 involved problem 3-d cnns one
0 8 these 3-d demonstrated one model
0 9 each belief one model machine
0 10 neural groups backpropagation ( when
0 11 cresceptron is ( boltzmann computer
0 12 and while by each success
0 13 first when each success supervised
0 14 but anns success supervised units
0 15 each success results units working
0 16 similar deep units working human
0 17 produced deng results similar these
0 18 system as combined 's first
0 19 algorithm since these first fine-tuning
0 20 as models neural network the
0 21 hinton ) algorithm an )
0 22 all algorithm treating ) rnns
0 23 colleagues difficulties ) rnns graphics
0 24 can deep rnns in than
0 25 and machine graphics than speech
0 26 been graphics than by groups
0 27 

0 1051 using a nvidia many-layered results
0 1052 workshop combined many-layered results one
0 1053 these 3-d results one turn
0 1054 each results one turn systems
0 1055 and machine data paper ''
0 1056 using data deep '' how
0 1057 one then with these nvidia
0 1058 used with according could human
0 1059 with according nvidia human ,
0 1060 can nvidia human , ctc
0 1061 using human , ctc system
0 1062 as processing ctc neural one
0 1063 deep-learning first community one a
0 1064 which community times a technology
0 1065 all produced a 2009 hinton
0 1066 using a 2009 hinton deep
0 1067 including using 2009 ( (
0 1068 using human deep when ''
0 1069 using ( microsoft '' data
0 1070 as when “ turn boolean
0 1071 and machine data boolean a
0 1072 using a technology a 2009
0 1073 hinton up a 2009 cluttered
0 1074 using a 2009 cluttered system
0 1075 colleagues then cluttered system gpus
0 1076 object cluttered system gradient ''
0 1077 lstm working gradient “ a
0 1078 handcrafted unsupervi

Epoch:0039 cost:4.582099915
Epoch:0040 cost:4.605824471
Epoch:0041 cost:4.570101738
Epoch:0042 cost:4.590951920
Epoch:0043 cost:4.558942795
Epoch:0044 cost:4.577247143
Epoch:0045 cost:4.548527718
Epoch:0046 cost:4.564617157
Epoch:0047 cost:4.538770199
Epoch:0048 cost:4.552944183
Epoch:0049 cost:4.529597282
Epoch:0050 cost:4.542119503
Epoch:0051 cost:4.520948410
Epoch:0052 cost:4.532045841
Epoch:0053 cost:4.512769699
Epoch:0054 cost:4.522636890
Epoch:0055 cost:4.505016327
Epoch:0056 cost:4.513818741
Epoch:0057 cost:4.497645378
Epoch:0058 cost:4.505523682
Epoch:0059 cost:4.490622997
Epoch:0060 cost:4.497697830
Epoch:0061 cost:4.483917713
Epoch:0062 cost:4.490289688
Epoch:0063 cost:4.477500916
Epoch:0064 cost:4.483258724
Epoch:0065 cost:4.471349239
Epoch:0066 cost:4.476568222
Epoch:0067 cost:4.465441704
Epoch:0068 cost:4.470187187
Epoch:0069 cost:4.459759712
Epoch:0070 cost:4.464088917
Epoch:0071 cost:4.454287052
Epoch:0072 cost:4.458249569
Epoch:0073 cost:4.449009895
Epoch:0074 cost:4.45

100 944 of rnns brain rnns rnns
100 945 ( rnns rnns rnns rnns
100 946 ( rnns rnns rnns rnns
100 947 rnns rnns rnns rnns rnns
100 948 ( rnns rnns ” rnns
100 949 ( rnns rnns rnns rnns
100 950 rnns rnns rnns rnns rnns
100 951 units rnns rnns ” rnns
100 952 % rnns rnns rnns rnns
100 953 rnns rnns rnns rnns rnns
100 954 rnns rnns rnns rnns rnns
100 955 ( rnns rnns rnns rnns
100 956 of rnns rnns rnns rnns
100 957 of rnns rnns rnns rnns
100 958 of rnns rnns rnns rnns
100 959 % rnns rnns rnns rnns
100 960 % rnns rnns rnns rnns
100 961 of rnns rnns rnns rnns
100 962 of rnns rnns rnns rnns
100 963 ( rnns rnns rnns rnns
100 964 of rnns rnns rnns rnns
100 965 % rnns rnns rnns rnns
100 966 rnns rnns rnns rnns rnns
100 967 of rnns rnns rnns rnns
100 968 units rnns rnns rnns rnns
100 969 efficient rnns rnns rnns rnns
100 970 of rnns rnns rnns rnns
100 971 % rnns rnns rnns rnns
100 972 of rnns rnns rnns rnns
100 973 rnns rnns rnns rnns rnns
100 974 of rnns rnns rnns rnns
100 975 ( rnns rnns rnns rnns


Epoch:0133 cost:4.340341568
Epoch:0134 cost:4.341487408
Epoch:0135 cost:4.337442398
Epoch:0136 cost:4.338566303
Epoch:0137 cost:4.334550381
Epoch:0138 cost:4.335649490
Epoch:0139 cost:4.331662655
Epoch:0140 cost:4.332736015
Epoch:0141 cost:4.328778267
Epoch:0142 cost:4.329822540
Epoch:0143 cost:4.325894833
Epoch:0144 cost:4.326909065
Epoch:0145 cost:4.323010921
Epoch:0146 cost:4.323992729
Epoch:0147 cost:4.320125580
Epoch:0148 cost:4.321071625
Epoch:0149 cost:4.317237377
Epoch:0150 cost:4.318146706
Epoch:0151 cost:4.314345360
Epoch:0152 cost:4.315215111
Epoch:0153 cost:4.311447620
Epoch:0154 cost:4.312275887
Epoch:0155 cost:4.308543682
Epoch:0156 cost:4.309328556
Epoch:0157 cost:4.305633068
Epoch:0158 cost:4.306372166
Epoch:0159 cost:4.302713394
Epoch:0160 cost:4.303405762
Epoch:0161 cost:4.299785614
Epoch:0162 cost:4.300428391
Epoch:0163 cost:4.296847343
Epoch:0164 cost:4.297438145
Epoch:0165 cost:4.293898582
Epoch:0166 cost:4.294436455
Epoch:0167 cost:4.290938854
Epoch:0168 cost:4.29

...

2700 1276 brain experienced a ( (
2700 1277 ( a ( ( according
2700 1278 ” results at according boolean
2700 1279 ) at according boolean two
2700 1280 cnns 3-d began be recurrent
2700 1281 trained gradient two , nets
2700 1282 through schmidhuber et nets graphics
2700 1283 through temporal trained graphics called
2700 1284 of trained graphics handcrafted working
2700 1285 asr computer speaker generative these
2700 1286 features including generative have graphics
2700 1287 asr combined have graphics around
2700 1288 asr difficulties vision involved generative
2700 1289 rnns vision experienced rina pre-trained
2700 1290 asr experienced rina vision however
2700 1291 trained experienced vision % units
2700 1292 layers , then units experienced
2700 1293 to then layer experienced lstm
2700 1294 cresceptron success experienced graphics trained
2700 1295 difficulties experienced graphics trained %
2700 1296 cresceptron started mixture hinton (
2700 1297 called . % ( %
2700 1298 recognition hint

2800 1151 trained machine a ( (
2800 1152 asr survey ( ( (
2800 1153 ( % ( ( (
2800 1154 ( % ( ( (
2800 1155 ( a ( ( cnns
2800 1156 to that ( cnns et
2800 1157 ( a ( ( rina
2800 1158 including similar all rina have
2800 1159 asr experienced up have markov
2800 1160 % ( a according feedforward
2800 1161 ( a ( feedforward cresceptron
2800 1162 ) technology as called other
2800 1163 on introduced boltzmann other gaussian
2800 1164 asr boltzmann ( gaussian network
2800 1165 similar gradient a including paper
2800 1166 ( a ( ( rina
2800 1167 including taken an rina many-layered
2800 1168 asr that workshop from all
2800 1169 neural times hinton paper rina
2800 1170 in however all rina working
2800 1171 asr experienced algorithm have microsoft
2800 1172 % rnns by et a
2800 1173 through schmidhuber 2009 ( (
2800 1174 ( % ( ( (
2800 1175 ( a ( ( (
2800 1176 through then are problem %
2800 1177 ( experienced ( ( (
2800 1178 ( % ( ( (
2800 1179 ( % ( ( (
2800 1180 ( % ( ( (
2800 1181 ( a machine 

Epoch:2843 cost:0.934777617
Epoch:2844 cost:0.933844388
Epoch:2845 cost:0.934518993
Epoch:2846 cost:0.933616102
Epoch:2847 cost:0.934252977
Epoch:2848 cost:0.933377922
Epoch:2849 cost:0.933958054
Epoch:2850 cost:0.933099031
Epoch:2851 cost:0.933624268
Epoch:2852 cost:0.932769418
Epoch:2853 cost:0.933253884
Epoch:2854 cost:0.932397485
Epoch:2855 cost:0.932855010
Epoch:2856 cost:0.931996465
Epoch:2857 cost:0.932436943
Epoch:2858 cost:0.931577444
Epoch:2859 cost:0.932007551
Epoch:2860 cost:0.931148410
Epoch:2861 cost:0.931573391
Epoch:2862 cost:0.930715084
Epoch:2863 cost:0.931139410
Epoch:2864 cost:0.930281520
Epoch:2865 cost:0.930710316
Epoch:2866 cost:0.929851532
Epoch:2867 cost:0.930289924
Epoch:2868 cost:0.929428399
Epoch:2869 cost:0.929882169
Epoch:2870 cost:0.929015636
Epoch:2871 cost:0.929491162
Epoch:2872 cost:0.928617001
Epoch:2873 cost:0.929121017
Epoch:2874 cost:0.928236723
Epoch:2875 cost:0.928776145
Epoch:2876 cost:0.927879691
Epoch:2877 cost:0.928460777
Epoch:2878 cost:0.92

2900 1037 ” that at data %
2900 1038 ( % ( ( (
2900 1039 ( a ( ( (
2900 1040 ” trained ( ( pre-trained
2900 1041 colleagues workshop ( similar began
2900 1042 ( a ( ( lstm
2900 1043 ” however technology lstm called
2900 1044 ) technology as called (
2900 1045 rnns ( ( ( later
2900 1046 features recurrent gaussian speaker (
2900 1047 ( % ( ( first
2900 1048 ( % ( into recurrent
2900 1049 through one ( ( (
2900 1050 ( % ( ( 3-d
2900 1051 ( a ( brain boolean
2900 1052 ) at lstm boolean machine
2900 1053 cnns 3-d boolean be %
2900 1054 trained technology technology gaussian (
2900 1055 colleagues workshop ( similar been
2900 1056 ( % machine been lstm
2900 1057 into then been lstm human
2900 1058 pre-trained trained generative unsupervised speaker
2900 1059 cresceptron generative ( sri have
2900 1060 trained experienced speaker machine nvidia
2900 1061 ( % machine to around
2900 1062 % big to evaluation that
2900 1063 asr rnns two by a
2900 1064 including combined schmidhuber a that
2900 1

Epoch:2938 cost:0.917123556
Epoch:2939 cost:0.917689800
Epoch:2940 cost:0.916807890
Epoch:2941 cost:0.917386293
Epoch:2942 cost:0.916500092
Epoch:2943 cost:0.917091966
Epoch:2944 cost:0.916201234
Epoch:2945 cost:0.916807950
Epoch:2946 cost:0.915913463
Epoch:2947 cost:0.916537106
Epoch:2948 cost:0.915642381
Epoch:2949 cost:0.916283846
Epoch:2950 cost:0.915396333
Epoch:2951 cost:0.916050494
Epoch:2952 cost:0.915182054
Epoch:2953 cost:0.915830135
Epoch:2954 cost:0.914990723
Epoch:2955 cost:0.915602386
Epoch:2956 cost:0.914789677
Epoch:2957 cost:0.915344775
Epoch:2958 cost:0.914545953
Epoch:2959 cost:0.915046871
Epoch:2960 cost:0.914249659
Epoch:2961 cost:0.914711118
Epoch:2962 cost:0.913910627
Epoch:2963 cost:0.914346099
Epoch:2964 cost:0.913542330
Epoch:2965 cost:0.913960993
Epoch:2966 cost:0.913156211
Epoch:2967 cost:0.913563550
Epoch:2968 cost:0.912759781
Epoch:2969 cost:0.913160086
Epoch:2970 cost:0.912358403
Epoch:2971 cost:0.912755489
Epoch:2972 cost:0.911956072
Epoch:2973 cost:0.91

In [5]:
tf.reset_default_graph()
tf.set_random_seed(123)

class Model():
    '''
    Dynamic RNN using the BasicRNNCell API
    '''
    def __init__(self):
        # attach a session to tensorflow
        self.sess = tf.Session()
        self.build_graph()
        self.sess.run(tf.global_variables_initializer())
        
    def build_graph(self):
                   
        # Step 1: construct the inputs
        self.x = tf.placeholder(tf.int32, (batch_size, sequence_length))
        self.y = tf.placeholder(tf.int32, (batch_size, sequence_length))
        x_one_hot = tf.one_hot(self.x, vocab_size)
        # construct the words in a single sentence as a 
        # list of individual training instances
        
        # Step 2: Calculate the states for each time step
        # initialize the state to zeros(s_0)
        rnn_cell = tf.contrib.rnn.BasicRNNCell(hidden_size)
        s0 = tf.zeros((batch_size, hidden_size))
        self.states, _ = tf.nn.dynamic_rnn(rnn_cell, x_one_hot, initial_state=s0)
        
        # Step 3: Calculate the losses
        # Declare the variable for the softmax layer
        V = tf.get_variable('V',(hidden_size,vocab_size),dtype=tf.float32)
        logits = tf.reshape(
            tf.matmul(tf.reshape(self.states, [-1,hidden_size]),V),
            [batch_size, sequence_length, vocab_size])
        self.predictions = tf.nn.softmax(logits)
        # labels: Tensor with each entry in [0,num_classes)
        # refer to: https://stackoverflow.com/questions/37312421/tensorflow-whats-the-difference-between-sparse-softmax-cross-entropy-with-logi
        losses = tf.nn.sparse_softmax_cross_entropy_with_logits(
        logits = logits, labels = self.y)
        self.cost = tf.reduce_mean(losses) # average cross-entropy loss
        self.optimizer =\
        tf.train.AdagradOptimizer(learning_rate).minimize(self.cost)
            
    def train(self, x, y):
        return self.sess.run([self.cost,
                              self.optimizer,
                              self.states],
                            feed_dict={self.x:x,self.y:y})
m = Model()

print('Learning Started')

for epoch in range(n_epochs):
    c, _, pred = m.train(dataX, dataY)
    print('Epoch:%04d' %(epoch+1),'cost:%.9f' % c)
    if epoch % 100 == 0:
        # predict the words using the softmax value
        for j,batch in enumerate(np.argmax(np.array(pred),axis=2).T):
            words = ' '.join([id2word[i] for i in batch])
            print(epoch,j,words)

print('Learning Finished')

Learning Started
Epoch:0001 cost:5.707500458
0 0 trained many-layered workshop when working involved published human learning object restricted 2006 workshop published working object et markov an hardware asr first involved from layers workshop started many dnns markov feature demonstrated from dnns asr neural involved asr published including nets trained asr up involved speech success from days cluttered lstm when asr speech object learning more dnns many dnns trained asr layers involved when which markov use involved speed involved from started algorithm time markov late called with an many into features automatic computer were demonstrated technology units when al involved learned brain technology asr boolean hardware neural survey it features working involved cascade belief systems trained published asr data workshop object how trained when days cascade evaluation used 1990s published . nets published system used could treating microsoft are published including lstm from hardware n

Epoch:0047 cost:4.534517288
Epoch:0048 cost:4.548113823
Epoch:0049 cost:4.525043964
Epoch:0050 cost:4.536652565
Epoch:0051 cost:4.516110420
Epoch:0052 cost:4.526052952
Epoch:0053 cost:4.507674217
Epoch:0054 cost:4.516219139
Epoch:0055 cost:4.499693394
Epoch:0056 cost:4.507066250
Epoch:0057 cost:4.492132187
Epoch:0058 cost:4.498519421
Epoch:0059 cost:4.484954834
Epoch:0060 cost:4.490511417
Epoch:0061 cost:4.478129387
Epoch:0062 cost:4.482983112
Epoch:0063 cost:4.471627235
Epoch:0064 cost:4.475884438
Epoch:0065 cost:4.465419769
Epoch:0066 cost:4.469169617
Epoch:0067 cost:4.459483147
Epoch:0068 cost:4.462800503
Epoch:0069 cost:4.453794956
Epoch:0070 cost:4.456743240
Epoch:0071 cost:4.448335648
Epoch:0072 cost:4.450967789
Epoch:0073 cost:4.443086624
Epoch:0074 cost:4.445448399
Epoch:0075 cost:4.438032150
Epoch:0076 cost:4.440162659
Epoch:0077 cost:4.433157921
Epoch:0078 cost:4.435092449
Epoch:0079 cost:4.428450584
Epoch:0080 cost:4.430218697
Epoch:0081 cost:4.423898697
Epoch:0082 cost:4.42

Epoch:0104 cost:4.382564545
Epoch:0105 cost:4.378026009
Epoch:0106 cost:4.379203796
Epoch:0107 cost:4.374703407
Epoch:0108 cost:4.375900745
Epoch:0109 cost:4.371427059
Epoch:0110 cost:4.372647285
Epoch:0111 cost:4.368191719
Epoch:0112 cost:4.369437218
Epoch:0113 cost:4.364993095
Epoch:0114 cost:4.366264343
Epoch:0115 cost:4.361825466
Epoch:0116 cost:4.363122940
Epoch:0117 cost:4.358684540
Epoch:0118 cost:4.360007286
Epoch:0119 cost:4.355566502
Epoch:0120 cost:4.356912613
Epoch:0121 cost:4.352466583
Epoch:0122 cost:4.353834152
Epoch:0123 cost:4.349381924
Epoch:0124 cost:4.350768089
Epoch:0125 cost:4.346309185
Epoch:0126 cost:4.347710609
Epoch:0127 cost:4.343245506
Epoch:0128 cost:4.344658852
Epoch:0129 cost:4.340188980
Epoch:0130 cost:4.341609955
Epoch:0131 cost:4.337137222
Epoch:0132 cost:4.338562012
Epoch:0133 cost:4.334088802
Epoch:0134 cost:4.335512638
Epoch:0135 cost:4.331041336
Epoch:0136 cost:4.332459927
Epoch:0137 cost:4.327993870
Epoch:0138 cost:4.329402924
Epoch:0139 cost:4.32

Epoch:0204 cost:4.220533371
Epoch:0205 cost:4.217613220
Epoch:0206 cost:4.216921806
Epoch:0207 cost:4.214052200
Epoch:0208 cost:4.213291168
Epoch:0209 cost:4.210470676
Epoch:0210 cost:4.209642410
Epoch:0211 cost:4.206868649
Epoch:0212 cost:4.205975533
Epoch:0213 cost:4.203246117
Epoch:0214 cost:4.202291012
Epoch:0215 cost:4.199603081
Epoch:0216 cost:4.198588848
Epoch:0217 cost:4.195939064
Epoch:0218 cost:4.194869041
Epoch:0219 cost:4.192255974
Epoch:0220 cost:4.191132069
Epoch:0221 cost:4.188551426
Epoch:0222 cost:4.187378407
Epoch:0223 cost:4.184827805
Epoch:0224 cost:4.183607578
Epoch:0225 cost:4.181083679
Epoch:0226 cost:4.179819584
Epoch:0227 cost:4.177320480
Epoch:0228 cost:4.176015377
Epoch:0229 cost:4.173537731
Epoch:0230 cost:4.172195435
Epoch:0231 cost:4.169735432
Epoch:0232 cost:4.168358803
Epoch:0233 cost:4.165914536
Epoch:0234 cost:4.164505959
Epoch:0235 cost:4.162075043
Epoch:0236 cost:4.160638809
Epoch:0237 cost:4.158216953
Epoch:0238 cost:4.156755447
Epoch:0239 cost:4.15

Epoch:0308 cost:4.008441925
Epoch:0309 cost:4.005259991
Epoch:0310 cost:4.003708363
Epoch:0311 cost:4.000517368
Epoch:0312 cost:3.998946905
Epoch:0313 cost:3.995747805
Epoch:0314 cost:3.994157791
Epoch:0315 cost:3.990951061
Epoch:0316 cost:3.989338875
Epoch:0317 cost:3.986126423
Epoch:0318 cost:3.984490395
Epoch:0319 cost:3.981273651
Epoch:0320 cost:3.979611397
Epoch:0321 cost:3.976392984
Epoch:0322 cost:3.974702597
Epoch:0323 cost:3.971484661
Epoch:0324 cost:3.969764471
Epoch:0325 cost:3.966549873
Epoch:0326 cost:3.964798927
Epoch:0327 cost:3.961589813
Epoch:0328 cost:3.959805965
Epoch:0329 cost:3.956605196
Epoch:0330 cost:3.954787731
Epoch:0331 cost:3.951597691
Epoch:0332 cost:3.949744701
Epoch:0333 cost:3.946567774
Epoch:0334 cost:3.944678307
Epoch:0335 cost:3.941516161
Epoch:0336 cost:3.939588308
Epoch:0337 cost:3.936444283
Epoch:0338 cost:3.934475183
Epoch:0339 cost:3.931351185
Epoch:0340 cost:3.929338932
Epoch:0341 cost:3.926237583
Epoch:0342 cost:3.924179554
Epoch:0343 cost:3.92

...

Epoch:2504 cost:1.007237792
Epoch:2505 cost:1.008014321
Epoch:2506 cost:1.006674528
Epoch:2507 cost:1.007443786
Epoch:2508 cost:1.006134748
Epoch:2509 cost:1.006897330
Epoch:2510 cost:1.005614758
Epoch:2511 cost:1.006370783
Epoch:2512 cost:1.005110979
Epoch:2513 cost:1.005860806
Epoch:2514 cost:1.004620075
Epoch:2515 cost:1.005364060
Epoch:2516 cost:1.004139304
Epoch:2517 cost:1.004877567
Epoch:2518 cost:1.003666401
Epoch:2519 cost:1.004399300
Epoch:2520 cost:1.003199339
Epoch:2521 cost:1.003926754
Epoch:2522 cost:1.002736449
Epoch:2523 cost:1.003458500
Epoch:2524 cost:1.002276659
Epoch:2525 cost:1.002993226
Epoch:2526 cost:1.001818419
Epoch:2527 cost:1.002529860
Epoch:2528 cost:1.001361370
Epoch:2529 cost:1.002067566
Epoch:2530 cost:1.000904799
Epoch:2531 cost:1.001605511
Epoch:2532 cost:1.000447989
Epoch:2533 cost:1.001143217
Epoch:2534 cost:0.999990284
Epoch:2535 cost:1.000679851
Epoch:2536 cost:0.999531269
Epoch:2537 cost:1.000214934
Epoch:2538 cost:0.999070346
Epoch:2539 cost:0.99

Epoch:2604 cost:0.983666778
Epoch:2605 cost:0.984441519
Epoch:2606 cost:0.983235061
Epoch:2607 cost:0.984011769
Epoch:2608 cost:0.982816815
Epoch:2609 cost:0.983591855
Epoch:2610 cost:0.982410371
Epoch:2611 cost:0.983179927
Epoch:2612 cost:0.982013583
Epoch:2613 cost:0.982773781
Epoch:2614 cost:0.981624782
Epoch:2615 cost:0.982371807
Epoch:2616 cost:0.981241882
Epoch:2617 cost:0.981972337
Epoch:2618 cost:0.980862677
Epoch:2619 cost:0.981573343
Epoch:2620 cost:0.980484486
Epoch:2621 cost:0.981173158
Epoch:2622 cost:0.980104744
Epoch:2623 cost:0.980769634
Epoch:2624 cost:0.979720235
Epoch:2625 cost:0.980360508
Epoch:2626 cost:0.979328275
Epoch:2627 cost:0.979943514
Epoch:2628 cost:0.978926063
Epoch:2629 cost:0.979516685
Epoch:2630 cost:0.978511631
Epoch:2631 cost:0.979078174
Epoch:2632 cost:0.978084087
Epoch:2633 cost:0.978627503
Epoch:2634 cost:0.977643371
Epoch:2635 cost:0.978164494
Epoch:2636 cost:0.977190852
Epoch:2637 cost:0.977690458
Epoch:2638 cost:0.976728141
Epoch:2639 cost:0.97

Epoch:2709 cost:0.962059796
Epoch:2710 cost:0.960969567
Epoch:2711 cost:0.961637855
Epoch:2712 cost:0.960559726
Epoch:2713 cost:0.961227894
Epoch:2714 cost:0.960160255
Epoch:2715 cost:0.960827351
Epoch:2716 cost:0.959769189
Epoch:2717 cost:0.960433900
Epoch:2718 cost:0.959384859
Epoch:2719 cost:0.960045934
Epoch:2720 cost:0.959005654
Epoch:2721 cost:0.959661484
Epoch:2722 cost:0.958630025
Epoch:2723 cost:0.959279478
Epoch:2724 cost:0.958256960
Epoch:2725 cost:0.958898544
Epoch:2726 cost:0.957885087
Epoch:2727 cost:0.958517671
Epoch:2728 cost:0.957513750
Epoch:2729 cost:0.958135903
Epoch:2730 cost:0.957141757
Epoch:2731 cost:0.957752705
Epoch:2732 cost:0.956768334
Epoch:2733 cost:0.957367241
Epoch:2734 cost:0.956392765
Epoch:2735 cost:0.956979036
Epoch:2736 cost:0.956014276
Epoch:2737 cost:0.956587374
Epoch:2738 cost:0.955632210
Epoch:2739 cost:0.956191778
Epoch:2740 cost:0.955245972
Epoch:2741 cost:0.955792069
Epoch:2742 cost:0.954855204
Epoch:2743 cost:0.955387712
Epoch:2744 cost:0.95

Epoch:2814 cost:0.940674603
Epoch:2815 cost:0.941283107
Epoch:2816 cost:0.940282285
Epoch:2817 cost:0.940899849
Epoch:2818 cost:0.939904273
Epoch:2819 cost:0.940529823
Epoch:2820 cost:0.939539075
Epoch:2821 cost:0.940171003
Epoch:2822 cost:0.939185321
Epoch:2823 cost:0.939822018
Epoch:2824 cost:0.938841879
Epoch:2825 cost:0.939481020
Epoch:2826 cost:0.938507795
Epoch:2827 cost:0.939146876
Epoch:2828 cost:0.938181996
Epoch:2829 cost:0.938818574
Epoch:2830 cost:0.937863886
Epoch:2831 cost:0.938495278
Epoch:2832 cost:0.937552750
Epoch:2833 cost:0.938176036
Epoch:2834 cost:0.937247336
Epoch:2835 cost:0.937859654
Epoch:2836 cost:0.936946154
Epoch:2837 cost:0.937545240
Epoch:2838 cost:0.936647534
Epoch:2839 cost:0.937230825
Epoch:2840 cost:0.936348438
Epoch:2841 cost:0.936914086
Epoch:2842 cost:0.936045766
Epoch:2843 cost:0.936591983
Epoch:2844 cost:0.935735524
Epoch:2845 cost:0.936260939
Epoch:2846 cost:0.935413539
Epoch:2847 cost:0.935917199
Epoch:2848 cost:0.935076356
Epoch:2849 cost:0.93

Epoch:2919 cost:0.922852576
Epoch:2920 cost:0.921895146
Epoch:2921 cost:0.922422528
Epoch:2922 cost:0.921478629
Epoch:2923 cost:0.922013164
Epoch:2924 cost:0.921080947
Epoch:2925 cost:0.921622753
Epoch:2926 cost:0.920699775
Epoch:2927 cost:0.921248555
Epoch:2928 cost:0.920333147
Epoch:2929 cost:0.920888782
Epoch:2930 cost:0.919979393
Epoch:2931 cost:0.920541227
Epoch:2932 cost:0.919636667
Epoch:2933 cost:0.920204043
Epoch:2934 cost:0.919303656
Epoch:2935 cost:0.919875324
Epoch:2936 cost:0.918978810
Epoch:2937 cost:0.919553757
Epoch:2938 cost:0.918661177
Epoch:2939 cost:0.919237792
Epoch:2940 cost:0.918349802
Epoch:2941 cost:0.918926537
Epoch:2942 cost:0.918043911
Epoch:2943 cost:0.918618977
Epoch:2944 cost:0.917742908
Epoch:2945 cost:0.918314338
Epoch:2946 cost:0.917445898
Epoch:2947 cost:0.918011844
Epoch:2948 cost:0.917152643
Epoch:2949 cost:0.917711020
Epoch:2950 cost:0.916862130
Epoch:2951 cost:0.917410970
Epoch:2952 cost:0.916573584
Epoch:2953 cost:0.917111218
Epoch:2954 cost:0.91

In [6]:
tf.reset_default_graph()
tf.set_random_seed(123)

class Model():
    '''
    Dynamic RNN using the BasicRNNCell API and sequence_loss
    '''
    def __init__(self):
        # attach a session to tensorflow
        self.sess = tf.Session()
        self.build_graph()
        self.sess.run(tf.global_variables_initializer())
        
    def build_graph(self):
                   
        # Step 1: construct the inputs
        self.x = tf.placeholder(tf.int32, (batch_size, sequence_length))
        self.y = tf.placeholder(tf.int32, (batch_size, sequence_length))
        x_one_hot = tf.one_hot(self.x, vocab_size)
        # construct the words in a single sentence as a 
        # list of individual training instances
        
        # Step 2: Calculate the states for each time step
        # initialize the state to zeros(s_0)
        rnn_cell = tf.contrib.rnn.BasicRNNCell(hidden_size)
        s0 = tf.zeros((batch_size, hidden_size))
        self.states, _ = tf.nn.dynamic_rnn(rnn_cell, x_one_hot, initial_state=s0)
        
        # Step 3: Calculate the losses
        # Declare the variable for the softmax layer
        V = tf.get_variable('V',(hidden_size,vocab_size),dtype=tf.float32)
        logits = tf.reshape(
            tf.matmul(tf.reshape(self.states, [-1,hidden_size]),V),
            [batch_size, sequence_length, vocab_size])
        self.predictions = tf.nn.softmax(logits)
        
        weights = tf.ones([batch_size, sequence_length])
        sequence_loss = tf.contrib.seq2seq.sequence_loss(
        logits=logits, targets=self.y, weights=weights)
        self.cost = tf.reduce_mean(sequence_loss) # average cross-entropy loss
        
        self.optimizer =\
        tf.train.AdagradOptimizer(learning_rate).minimize(self.cost)
            
    def train(self, x, y):
        return self.sess.run([self.cost,
                              self.optimizer,
                              self.states],
                            feed_dict={self.x:x,self.y:y})
m = Model()

print('Learning Started')

for epoch in range(n_epochs):
    c, _, pred = m.train(dataX, dataY)
    print('Epoch:%04d' %(epoch+1),'cost:%.9f' % c)
    if epoch % 100 == 0:
        # predict the words using the softmax value
        for j,batch in enumerate(np.argmax(np.array(pred),axis=2).T):
            words = ' '.join([id2word[i] for i in batch])
            print(epoch,j,words)

print('Learning Finished')

Learning Started
Epoch:0001 cost:5.707500458
0 0 trained many-layered workshop when working involved published human learning object restricted 2006 workshop published working object et markov an hardware asr first involved from layers workshop started many dnns markov feature demonstrated from dnns asr neural involved asr published including nets trained asr up involved speech success from days cluttered lstm when asr speech object learning more dnns many dnns trained asr layers involved when which markov use involved speed involved from started algorithm time markov late called with an many into features automatic computer were demonstrated technology units when al involved learned brain technology asr boolean hardware neural survey it features working involved cascade belief systems trained published asr data workshop object how trained when days cascade evaluation used 1990s published . nets published system used could treating microsoft are published including lstm from hardware n

Epoch:0047 cost:4.534517765
Epoch:0048 cost:4.548114300
Epoch:0049 cost:4.525043964
Epoch:0050 cost:4.536653042
Epoch:0051 cost:4.516110897
Epoch:0052 cost:4.526052952
Epoch:0053 cost:4.507673740
Epoch:0054 cost:4.516219139
Epoch:0055 cost:4.499693871
Epoch:0056 cost:4.507066727
Epoch:0057 cost:4.492132187
Epoch:0058 cost:4.498519421
Epoch:0059 cost:4.484955311
Epoch:0060 cost:4.490510941
Epoch:0061 cost:4.478129864
Epoch:0062 cost:4.482983589
Epoch:0063 cost:4.471627712
Epoch:0064 cost:4.475884914
Epoch:0065 cost:4.465419769
Epoch:0066 cost:4.469170094
Epoch:0067 cost:4.459483624
Epoch:0068 cost:4.462801456
Epoch:0069 cost:4.453795433
Epoch:0070 cost:4.456743240
Epoch:0071 cost:4.448335171
Epoch:0072 cost:4.450967789
Epoch:0073 cost:4.443086624
Epoch:0074 cost:4.445447922
Epoch:0075 cost:4.438032627
Epoch:0076 cost:4.440163136
Epoch:0077 cost:4.433157921
Epoch:0078 cost:4.435092449
Epoch:0079 cost:4.428450584
Epoch:0080 cost:4.430218697
Epoch:0081 cost:4.423898697
Epoch:0082 cost:4.42

Epoch:0150 cost:4.310899734
Epoch:0151 cost:4.306550980
Epoch:0152 cost:4.307778835
Epoch:0153 cost:4.303458691
Epoch:0154 cost:4.304644108
Epoch:0155 cost:4.300356388
Epoch:0156 cost:4.301495075
Epoch:0157 cost:4.297242641
Epoch:0158 cost:4.298331738
Epoch:0159 cost:4.294116974
Epoch:0160 cost:4.295152664
Epoch:0161 cost:4.290978432
Epoch:0162 cost:4.291956425
Epoch:0163 cost:4.287826061
Epoch:0164 cost:4.288743973
Epoch:0165 cost:4.284660339
Epoch:0166 cost:4.285513878
Epoch:0167 cost:4.281479359
Epoch:0168 cost:4.282265663
Epoch:0169 cost:4.278283119
Epoch:0170 cost:4.278999805
Epoch:0171 cost:4.275070190
Epoch:0172 cost:4.275714874
Epoch:0173 cost:4.271841049
Epoch:0174 cost:4.272411823
Epoch:0175 cost:4.268594742
Epoch:0176 cost:4.269089222
Epoch:0177 cost:4.265331268
Epoch:0178 cost:4.265747547
Epoch:0179 cost:4.262049198
Epoch:0180 cost:4.262386799
Epoch:0181 cost:4.258749008
Epoch:0182 cost:4.259005547
Epoch:0183 cost:4.255430698
Epoch:0184 cost:4.255606174
Epoch:0185 cost:4.25

200 2 learning learning learning learning learning learning learning started learning learning learning learning learning learning learning learning started learning learning learning learning learning learning learning learning learning learning learning started learning learning learning learning learning learning learning learning learning learning learning learning learning started learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning started learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning learning 

Epoch:0252 cost:4.129189014
Epoch:0253 cost:4.126746655
Epoch:0254 cost:4.125202656
Epoch:0255 cost:4.122744083
Epoch:0256 cost:4.121205330
Epoch:0257 cost:4.118727684
Epoch:0258 cost:4.117197037
Epoch:0259 cost:4.114697456
Epoch:0260 cost:4.113179207
Epoch:0261 cost:4.110652924
Epoch:0262 cost:4.109148979
Epoch:0263 cost:4.106593132
Epoch:0264 cost:4.105106354
Epoch:0265 cost:4.102516651
Epoch:0266 cost:4.101048470
Epoch:0267 cost:4.098422050
Epoch:0268 cost:4.096973896
Epoch:0269 cost:4.094305992
Epoch:0270 cost:4.092877865
Epoch:0271 cost:4.090166092
Epoch:0272 cost:4.088756084
Epoch:0273 cost:4.085998535
Epoch:0274 cost:4.084604263
Epoch:0275 cost:4.081799984
Epoch:0276 cost:4.080418587
Epoch:0277 cost:4.077567577
Epoch:0278 cost:4.076193810
Epoch:0279 cost:4.073297501
Epoch:0280 cost:4.071927547
Epoch:0281 cost:4.068989277
Epoch:0282 cost:4.067617893
Epoch:0283 cost:4.064640999
Epoch:0284 cost:4.063264847
Epoch:0285 cost:4.060253620
Epoch:0286 cost:4.058869362
Epoch:0287 cost:4.05

...

Epoch:2507 cost:1.007411242
Epoch:2508 cost:1.006129026
Epoch:2509 cost:1.006932497
Epoch:2510 cost:1.005640745
Epoch:2511 cost:1.006467462
Epoch:2512 cost:1.005165100
Epoch:2513 cost:1.006018043
Epoch:2514 cost:1.004704833
Epoch:2515 cost:1.005585074
Epoch:2516 cost:1.004261732
Epoch:2517 cost:1.005167484
Epoch:2518 cost:1.003835678
Epoch:2519 cost:1.004762053
Epoch:2520 cost:1.003424644
Epoch:2521 cost:1.004363060
Epoch:2522 cost:1.003022909
Epoch:2523 cost:1.003962159
Epoch:2524 cost:1.002621889
Epoch:2525 cost:1.003549457
Epoch:2526 cost:1.002211332
Epoch:2527 cost:1.003116250
Epoch:2528 cost:1.001781344
Epoch:2529 cost:1.002655745
Epoch:2530 cost:1.001324534
Epoch:2531 cost:1.002165675
Epoch:2532 cost:1.000838280
Epoch:2533 cost:1.001647830
Epoch:2534 cost:1.000324488
Epoch:2535 cost:1.001107812
Epoch:2536 cost:0.999788761
Epoch:2537 cost:1.000553250
Epoch:2538 cost:0.999239266
Epoch:2539 cost:0.999992073
Epoch:2540 cost:0.998683929
Epoch:2541 cost:0.999432147
Epoch:2542 cost:0.99

Epoch:2612 cost:0.981676877
Epoch:2613 cost:0.982292354
Epoch:2614 cost:0.981277406
Epoch:2615 cost:0.981990397
Epoch:2616 cost:0.980939567
Epoch:2617 cost:0.981764019
Epoch:2618 cost:0.980681062
Epoch:2619 cost:0.981617868
Epoch:2620 cost:0.980512261
Epoch:2621 cost:0.981539547
Epoch:2622 cost:0.980421782
Epoch:2623 cost:0.981489956
Epoch:2624 cost:0.980363667
Epoch:2625 cost:0.981406927
Epoch:2626 cost:0.980263054
Epoch:2627 cost:0.981225610
Epoch:2628 cost:0.980045497
Epoch:2629 cost:0.980904102
Epoch:2630 cost:0.979673505
Epoch:2631 cost:0.980439007
Epoch:2632 cost:0.979156792
Epoch:2633 cost:0.979858518
Epoch:2634 cost:0.978538036
Epoch:2635 cost:0.979205668
Epoch:2636 cost:0.977867067
Epoch:2637 cost:0.978521526
Epoch:2638 cost:0.977183759
Epoch:2639 cost:0.977837026
Epoch:2640 cost:0.976514161
Epoch:2641 cost:0.977171659
Epoch:2642 cost:0.975871921
Epoch:2643 cost:0.976535738
Epoch:2644 cost:0.975262642
Epoch:2645 cost:0.975933492
Epoch:2646 cost:0.974686861
Epoch:2647 cost:0.97

Epoch:2716 cost:0.959722936
Epoch:2717 cost:0.960289359
Epoch:2718 cost:0.959305108
Epoch:2719 cost:0.959911227
Epoch:2720 cost:0.958908737
Epoch:2721 cost:0.959563971
Epoch:2722 cost:0.958541453
Epoch:2723 cost:0.959253728
Epoch:2724 cost:0.958211303
Epoch:2725 cost:0.958984673
Epoch:2726 cost:0.957925081
Epoch:2727 cost:0.958755553
Epoch:2728 cost:0.957684100
Epoch:2729 cost:0.958556652
Epoch:2730 cost:0.957479715
Epoch:2731 cost:0.958367884
Epoch:2732 cost:0.957289338
Epoch:2733 cost:0.958160460
Epoch:2734 cost:0.957080305
Epoch:2735 cost:0.957904816
Epoch:2736 cost:0.956818759
Epoch:2737 cost:0.957579613
Epoch:2738 cost:0.956482351
Epoch:2739 cost:0.957178354
Epoch:2740 cost:0.956067026
Epoch:2741 cost:0.956709802
Epoch:2742 cost:0.955585897
Epoch:2743 cost:0.956192017
Epoch:2744 cost:0.955060780
Epoch:2745 cost:0.955645740
Epoch:2746 cost:0.954513669
Epoch:2747 cost:0.955090165
Epoch:2748 cost:0.953963280
Epoch:2749 cost:0.954539359
Epoch:2750 cost:0.953422010
Epoch:2751 cost:0.95

Epoch:2821 cost:0.939894617
Epoch:2822 cost:0.939113438
Epoch:2823 cost:0.939492643
Epoch:2824 cost:0.938701630
Epoch:2825 cost:0.939114392
Epoch:2826 cost:0.938307881
Epoch:2827 cost:0.938765824
Epoch:2828 cost:0.937938333
Epoch:2829 cost:0.938454449
Epoch:2830 cost:0.937601686
Epoch:2831 cost:0.938189209
Epoch:2832 cost:0.937308908
Epoch:2833 cost:0.937978745
Epoch:2834 cost:0.937072158
Epoch:2835 cost:0.937828302
Epoch:2836 cost:0.936900616
Epoch:2837 cost:0.937733054
Epoch:2838 cost:0.936792076
Epoch:2839 cost:0.937672138
Epoch:2840 cost:0.936724246
Epoch:2841 cost:0.937607408
Epoch:2842 cost:0.936652064
Epoch:2843 cost:0.937491596
Epoch:2844 cost:0.936520159
Epoch:2845 cost:0.937284768
Epoch:2846 cost:0.936286151
Epoch:2847 cost:0.936969519
Epoch:2848 cost:0.935936928
Epoch:2849 cost:0.936553061
Epoch:2850 cost:0.935489058
Epoch:2851 cost:0.936059833
Epoch:2852 cost:0.934974611
Epoch:2853 cost:0.935519814
Epoch:2854 cost:0.934426486
Epoch:2855 cost:0.934960246
Epoch:2856 cost:0.93

Epoch:2921 cost:0.922485590
Epoch:2922 cost:0.921721339
Epoch:2923 cost:0.922085345
Epoch:2924 cost:0.921328723
Epoch:2925 cost:0.921681762
Epoch:2926 cost:0.920932591
Epoch:2927 cost:0.921277463
Epoch:2928 cost:0.920535207
Epoch:2929 cost:0.920875192
Epoch:2930 cost:0.920138240
Epoch:2931 cost:0.920477211
Epoch:2932 cost:0.919743836
Epoch:2933 cost:0.920086205
Epoch:2934 cost:0.919353783
Epoch:2935 cost:0.919704735
Epoch:2936 cost:0.918969929
Epoch:2937 cost:0.919335365
Epoch:2938 cost:0.918594539
Epoch:2939 cost:0.918981493
Epoch:2940 cost:0.918230474
Epoch:2941 cost:0.918646872
Epoch:2942 cost:0.917881548
Epoch:2943 cost:0.918336332
Epoch:2944 cost:0.917552590
Epoch:2945 cost:0.918055952
Epoch:2946 cost:0.917250574
Epoch:2947 cost:0.917812169
Epoch:2948 cost:0.916984022
Epoch:2949 cost:0.917611122
Epoch:2950 cost:0.916761458
Epoch:2951 cost:0.917456150
Epoch:2952 cost:0.916589677
Epoch:2953 cost:0.917342961
Epoch:2954 cost:0.916466951
Epoch:2955 cost:0.917255878
Epoch:2956 cost:0.91

In [7]:
tf.reset_default_graph()
tf.set_random_seed(123)

class Model():
    '''
    Dynamic RNN using the BasicRNNCell API + sequence_loss + bias term in the softmax
    '''
    def __init__(self):
        # attach a session to tensorflow
        self.sess = tf.Session()
        self.build_graph()
        self.sess.run(tf.global_variables_initializer())
        
    def build_graph(self):
                   
        # Step 1: construct the inputs
        self.x = tf.placeholder(tf.int32, (batch_size, sequence_length))
        self.y = tf.placeholder(tf.int32, (batch_size, sequence_length))
        x_one_hot = tf.one_hot(self.x, vocab_size)
        # construct the words in a single sentence as a 
        # list of individual training instances
        
        # Step 2: Calculate the states for each time step
        # initialize the state to zeros(s_0)
        rnn_cell = tf.contrib.rnn.BasicRNNCell(hidden_size)
        s0 = tf.zeros((batch_size, hidden_size))
        self.states, _ = tf.nn.dynamic_rnn(rnn_cell, x_one_hot, initial_state=s0)
        print(self.states)
        
        # Step 3: Calculate the losses
        # Declare the variable for the softmax layer
        with tf.variable_scope('softmax'):
            W = tf.get_variable('V',(hidden_size,vocab_size),dtype=tf.float32)
            b = tf.get_variable('b',(vocab_size),initializer=tf.constant_initializer(0.0))
        logits = tf.reshape(
            tf.matmul(tf.reshape(self.states, [-1,hidden_size]),W) + b,
            [batch_size, sequence_length, vocab_size])
        self.predictions = tf.nn.softmax(logits)
        
        weights = tf.ones([batch_size, sequence_length])
        sequence_loss = tf.contrib.seq2seq.sequence_loss(
        logits=logits, targets=self.y, weights=weights)
        self.cost = tf.reduce_mean(sequence_loss) # average cross-entropy loss
        
        self.optimizer =\
        tf.train.AdagradOptimizer(learning_rate).minimize(self.cost)
            
    def train(self, x, y):
        return self.sess.run([self.cost,
                              self.optimizer,
                              self.states],
                            feed_dict={self.x:x,self.y:y})
m = Model()

print('Learning Started')

for epoch in range(n_epochs):
    c, _, pred = m.train(dataX, dataY)
    print('Epoch:%04d' %(epoch+1),'cost:%.9f' % c)
    if epoch % 500 == 0:
        # predict the words using the softmax value
        for j,batch in enumerate(np.argmax(np.array(pred),axis=2).T):
            words = ' '.join([id2word[i] for i in batch])
            print(epoch,j,words)

print('Learning Finished')

Tensor("rnn/transpose:0", shape=(1372, 5, 200), dtype=float32)
Learning Started
Epoch:0001 cost:5.707500458
0 0 trained many-layered workshop when working involved published human learning object restricted 2006 workshop published working object et markov an hardware asr first involved from layers workshop started many dnns markov feature demonstrated from dnns asr neural involved asr published including nets trained asr up involved speech success from days cluttered lstm when asr speech object learning more dnns many dnns trained asr layers involved when which markov use involved speed involved from started algorithm time markov late called with an many into features automatic computer were demonstrated technology units when al involved learned brain technology asr boolean hardware neural survey it features working involved cascade belief systems trained published asr data workshop object how trained when days cascade evaluation used 1990s published . nets published system used could 

Epoch:0017 cost:4.830160141
Epoch:0018 cost:4.795225143
Epoch:0019 cost:4.765226841
Epoch:0020 cost:4.747362137
Epoch:0021 cost:4.745476723
Epoch:0022 cost:4.829462051
Epoch:0023 cost:4.718296051
Epoch:0024 cost:4.809125423
Epoch:0025 cost:4.673831940
Epoch:0026 cost:4.716681957
Epoch:0027 cost:4.671919346
Epoch:0028 cost:4.756777287
Epoch:0029 cost:4.622113228
Epoch:0030 cost:4.639854431
Epoch:0031 cost:4.625120640
Epoch:0032 cost:4.681986809
Epoch:0033 cost:4.597506523
Epoch:0034 cost:4.626203537
Epoch:0035 cost:4.589648724
Epoch:0036 cost:4.625116348
Epoch:0037 cost:4.572971821
Epoch:0038 cost:4.598056316
Epoch:0039 cost:4.561336517
Epoch:0040 cost:4.583560944
Epoch:0041 cost:4.549528599
Epoch:0042 cost:4.567795277
Epoch:0043 cost:4.538670540
Epoch:0044 cost:4.553827763
Epoch:0045 cost:4.528542042
Epoch:0046 cost:4.541124821
Epoch:0047 cost:4.519061565
Epoch:0048 cost:4.529520988
Epoch:0049 cost:4.510168552
Epoch:0050 cost:4.518878460
Epoch:0051 cost:4.501809597
Epoch:0052 cost:4.50

Epoch:0323 cost:3.961429119
Epoch:0324 cost:3.959701538
Epoch:0325 cost:3.956409454
Epoch:0326 cost:3.954658747
Epoch:0327 cost:3.951365948
Epoch:0328 cost:3.949592829
Epoch:0329 cost:3.946301699
Epoch:0330 cost:3.944505692
Epoch:0331 cost:3.941216707
Epoch:0332 cost:3.939397812
Epoch:0333 cost:3.936111927
Epoch:0334 cost:3.934271336
Epoch:0335 cost:3.930988073
Epoch:0336 cost:3.929126024
Epoch:0337 cost:3.925844908
Epoch:0338 cost:3.923961163
Epoch:0339 cost:3.920683146
Epoch:0340 cost:3.918777704
Epoch:0341 cost:3.915502071
Epoch:0342 cost:3.913573980
Epoch:0343 cost:3.910300255
Epoch:0344 cost:3.908350945
Epoch:0345 cost:3.905077934
Epoch:0346 cost:3.903109074
Epoch:0347 cost:3.899836302
Epoch:0348 cost:3.897848368
Epoch:0349 cost:3.894574642
Epoch:0350 cost:3.892570257
Epoch:0351 cost:3.889294624
Epoch:0352 cost:3.887276173
Epoch:0353 cost:3.883996248
Epoch:0354 cost:3.881968498
Epoch:0355 cost:3.878681898
Epoch:0356 cost:3.876649857
Epoch:0357 cost:3.873351574
Epoch:0358 cost:3.87

Epoch:0521 cost:3.451624632
Epoch:0522 cost:3.437763691
Epoch:0523 cost:3.446158171
Epoch:0524 cost:3.434371948
Epoch:0525 cost:3.442727566
Epoch:0526 cost:3.432983875
Epoch:0527 cost:3.439678669
Epoch:0528 cost:3.429696321
Epoch:0529 cost:3.432397842
Epoch:0530 cost:3.422024727
Epoch:0531 cost:3.422357559
Epoch:0532 cost:3.413542032
Epoch:0533 cost:3.413266182
Epoch:0534 cost:3.406674862
Epoch:0535 cost:3.406321526
Epoch:0536 cost:3.402028799
Epoch:0537 cost:3.401478291
Epoch:0538 cost:3.399738312
Epoch:0539 cost:3.398162127
Epoch:0540 cost:3.399269342
Epoch:0541 cost:3.394926071
Epoch:0542 cost:3.398466587
Epoch:0543 cost:3.389772654
Epoch:0544 cost:3.394417048
Epoch:0545 cost:3.382349014
Epoch:0546 cost:3.387082815
Epoch:0547 cost:3.374629974
Epoch:0548 cost:3.379595757
Epoch:0549 cost:3.368607044
Epoch:0550 cost:3.374637604
Epoch:0551 cost:3.364669561
Epoch:0552 cost:3.372102737
Epoch:0553 cost:3.361412287
Epoch:0554 cost:3.368199348
Epoch:0555 cost:3.357985020
Epoch:0556 cost:3.36

Epoch:0822 cost:2.630065203
Epoch:0823 cost:2.622942209
Epoch:0824 cost:2.620909214
Epoch:0825 cost:2.616672993
Epoch:0826 cost:2.615892172
Epoch:0827 cost:2.613433361
Epoch:0828 cost:2.614020348
Epoch:0829 cost:2.611202240
Epoch:0830 cost:2.611315966
Epoch:0831 cost:2.605953932
Epoch:0832 cost:2.603172302
Epoch:0833 cost:2.597009182
Epoch:0834 cost:2.592609644
Epoch:0835 cost:2.588516712
Epoch:0836 cost:2.584569216
Epoch:0837 cost:2.584676266
Epoch:0838 cost:2.582435846
Epoch:0839 cost:2.591815710
Epoch:0840 cost:2.590757847
Epoch:0841 cost:2.613272429
Epoch:0842 cost:2.594884634
Epoch:0843 cost:2.605375767
Epoch:0844 cost:2.575467587
Epoch:0845 cost:2.573531628
Epoch:0846 cost:2.560507298
Epoch:0847 cost:2.561621428
Epoch:0848 cost:2.557087421
Epoch:0849 cost:2.566606522
Epoch:0850 cost:2.566039085
Epoch:0851 cost:2.585433483
Epoch:0852 cost:2.581823587
Epoch:0853 cost:2.595322371
Epoch:0854 cost:2.583783865
Epoch:0855 cost:2.579880238
Epoch:0856 cost:2.567612886
Epoch:0857 cost:2.55

...

Epoch:1802 cost:1.270503163
Epoch:1803 cost:1.270809174
Epoch:1804 cost:1.270011425
Epoch:1805 cost:1.269420266
Epoch:1806 cost:1.268544197
Epoch:1807 cost:1.267190456
Epoch:1808 cost:1.266119957
Epoch:1809 cost:1.264363408
Epoch:1810 cost:1.263105154
Epoch:1811 cost:1.261341453
Epoch:1812 cost:1.259981632
Epoch:1813 cost:1.258489251
Epoch:1814 cost:1.257119656
Epoch:1815 cost:1.256026030
Epoch:1816 cost:1.254703641
Epoch:1817 cost:1.254040241
Epoch:1818 cost:1.252784610
Epoch:1819 cost:1.252560735
Epoch:1820 cost:1.251368642
Epoch:1821 cost:1.251620412
Epoch:1822 cost:1.250475287
Epoch:1823 cost:1.251285672
Epoch:1824 cost:1.250150919
Epoch:1825 cost:1.251633644
Epoch:1826 cost:1.250424027
Epoch:1827 cost:1.252658486
Epoch:1828 cost:1.251194358
Epoch:1829 cost:1.254108906
Epoch:1830 cost:1.252103329
Epoch:1831 cost:1.255391479
Epoch:1832 cost:1.252563834
Epoch:1833 cost:1.255775690
Epoch:1834 cost:1.252083898
Epoch:1835 cost:1.254882336
Epoch:1836 cost:1.250630617
Epoch:1837 cost:1.25

Epoch:2044 cost:1.149927258
Epoch:2045 cost:1.151133895
Epoch:2046 cost:1.149091244
Epoch:2047 cost:1.150264263
Epoch:2048 cost:1.148232102
Epoch:2049 cost:1.149377465
Epoch:2050 cost:1.147354841
Epoch:2051 cost:1.148480892
Epoch:2052 cost:1.146466255
Epoch:2053 cost:1.147584319
Epoch:2054 cost:1.145575762
Epoch:2055 cost:1.146699071
Epoch:2056 cost:1.144693971
Epoch:2057 cost:1.145835757
Epoch:2058 cost:1.143831968
Epoch:2059 cost:1.145005107
Epoch:2060 cost:1.142999530
Epoch:2061 cost:1.144214630
Epoch:2062 cost:1.142204285
Epoch:2063 cost:1.143468380
Epoch:2064 cost:1.141449928
Epoch:2065 cost:1.142765999
Epoch:2066 cost:1.140734673
Epoch:2067 cost:1.142100930
Epoch:2068 cost:1.140051603
Epoch:2069 cost:1.141460896
Epoch:2070 cost:1.139388442
Epoch:2071 cost:1.140830040
Epoch:2072 cost:1.138729811
Epoch:2073 cost:1.140190125
Epoch:2074 cost:1.138059974
Epoch:2075 cost:1.139524460
Epoch:2076 cost:1.137365699
Epoch:2077 cost:1.138820648
Epoch:2078 cost:1.136639476
Epoch:2079 cost:1.13

Epoch:2342 cost:1.048475981
Epoch:2343 cost:1.049507856
Epoch:2344 cost:1.047943830
Epoch:2345 cost:1.048977494
Epoch:2346 cost:1.047416687
Epoch:2347 cost:1.048443794
Epoch:2348 cost:1.046890020
Epoch:2349 cost:1.047902346
Epoch:2350 cost:1.046359777
Epoch:2351 cost:1.047350764
Epoch:2352 cost:1.045823574
Epoch:2353 cost:1.046787858
Epoch:2354 cost:1.045279145
Epoch:2355 cost:1.046214223
Epoch:2356 cost:1.044727206
Epoch:2357 cost:1.045632005
Epoch:2358 cost:1.044168353
Epoch:2359 cost:1.045043707
Epoch:2360 cost:1.043605208
Epoch:2361 cost:1.044454098
Epoch:2362 cost:1.043041110
Epoch:2363 cost:1.043867469
Epoch:2364 cost:1.042480230
Epoch:2365 cost:1.043288946
Epoch:2366 cost:1.041926861
Epoch:2367 cost:1.042722940
Epoch:2368 cost:1.041386366
Epoch:2369 cost:1.042174101
Epoch:2370 cost:1.040862679
Epoch:2371 cost:1.041646004
Epoch:2372 cost:1.040360808
Epoch:2373 cost:1.041141987
Epoch:2374 cost:1.039884329
Epoch:2375 cost:1.040663838
Epoch:2376 cost:1.039436698
Epoch:2377 cost:1.04

Epoch:2535 cost:0.999229789
Epoch:2536 cost:0.997894049
Epoch:2537 cost:0.998743713
Epoch:2538 cost:0.997413516
Epoch:2539 cost:0.998264611
Epoch:2540 cost:0.996940613
Epoch:2541 cost:0.997792780
Epoch:2542 cost:0.996476531
Epoch:2543 cost:0.997328341
Epoch:2544 cost:0.996021450
Epoch:2545 cost:0.996871412
Epoch:2546 cost:0.995576024
Epoch:2547 cost:0.996421874
Epoch:2548 cost:0.995140374
Epoch:2549 cost:0.995979667
Epoch:2550 cost:0.994714916
Epoch:2551 cost:0.995544612
Epoch:2552 cost:0.994299591
Epoch:2553 cost:0.995116413
Epoch:2554 cost:0.993894339
Epoch:2555 cost:0.994694948
Epoch:2556 cost:0.993498325
Epoch:2557 cost:0.994279802
Epoch:2558 cost:0.993110418
Epoch:2559 cost:0.993869722
Epoch:2560 cost:0.992728293
Epoch:2561 cost:0.993463159
Epoch:2562 cost:0.992348909
Epoch:2563 cost:0.993057489
Epoch:2564 cost:0.991967559
Epoch:2565 cost:0.992649019
Epoch:2566 cost:0.991578758
Epoch:2567 cost:0.992232203
Epoch:2568 cost:0.991176426
Epoch:2569 cost:0.991801441
Epoch:2570 cost:0.99

Epoch:2875 cost:0.929292440
Epoch:2876 cost:0.928360045
Epoch:2877 cost:0.928970158
Epoch:2878 cost:0.928044379
Epoch:2879 cost:0.928650022
Epoch:2880 cost:0.927731752
Epoch:2881 cost:0.928330839
Epoch:2882 cost:0.927421093
Epoch:2883 cost:0.928012192
Epoch:2884 cost:0.927111983
Epoch:2885 cost:0.927693009
Epoch:2886 cost:0.926803410
Epoch:2887 cost:0.927372992
Epoch:2888 cost:0.926494181
Epoch:2889 cost:0.927050948
Epoch:2890 cost:0.926183283
Epoch:2891 cost:0.926726222
Epoch:2892 cost:0.925869286
Epoch:2893 cost:0.926397562
Epoch:2894 cost:0.925551057
Epoch:2895 cost:0.926063955
Epoch:2896 cost:0.925227046
Epoch:2897 cost:0.925724208
Epoch:2898 cost:0.924896002
Epoch:2899 cost:0.925377250
Epoch:2900 cost:0.924556792
Epoch:2901 cost:0.925021827
Epoch:2902 cost:0.924208641
Epoch:2903 cost:0.924657822
Epoch:2904 cost:0.923851490
Epoch:2905 cost:0.924284995
Epoch:2906 cost:0.923485518
Epoch:2907 cost:0.923903942
Epoch:2908 cost:0.923111379
Epoch:2909 cost:0.923515737
Epoch:2910 cost:0.92

In [8]:
tf.reset_default_graph()
tf.set_random_seed(123)

class Model():
    '''
    Dynamic RNN using the BasicRNNCell API + sequence_loss + FC layer(another way of doing softmax)
    '''
    def __init__(self):
        # attach a session to tensorflow
        self.sess = tf.Session()
        self.build_graph()
        self.sess.run(tf.global_variables_initializer())
        
    def build_graph(self):
                   
        # Step 1: construct the inputs
        self.x = tf.placeholder(tf.int32, (batch_size, sequence_length))
        self.y = tf.placeholder(tf.int32, (batch_size, sequence_length))
        x_one_hot = tf.one_hot(self.x, vocab_size)
        # construct the words in a single sentence as a 
        # list of individual training instances
        
        # Step 2: Calculate the states for each time step
        # initialize the state to zeros(s_0)
        rnn_cell = tf.contrib.rnn.BasicRNNCell(hidden_size)
        s0 = tf.zeros((batch_size, hidden_size))
        self.states, _ = tf.nn.dynamic_rnn(rnn_cell, x_one_hot, initial_state=s0)       
        
        # Step 3: Calculate the losses
        # FC layer(later used for softmax in calculation of sequence_loss)
        X_for_fc = tf.reshape(self.states, [-1, hidden_size])
        logits = tf.contrib.layers.fully_connected(X_for_fc, vocab_size, activation_fn=None)
        # reshape output from the softmax
        logits = tf.reshape(logits, [batch_size, sequence_length, vocab_size])
        
        weights = tf.ones([batch_size, sequence_length])
        sequence_loss = tf.contrib.seq2seq.sequence_loss(
        logits=logits, targets=self.y, weights=weights)
        self.cost = tf.reduce_mean(sequence_loss) # average cross-entropy loss
        
        self.optimizer =\
        tf.train.AdagradOptimizer(learning_rate).minimize(self.cost)
            
    def train(self, x, y):
        return self.sess.run([self.cost,
                              self.optimizer,
                              self.states],
                            feed_dict={self.x:x,self.y:y})
m = Model()

print('Learning Started')

for epoch in range(n_epochs):
    c, _, pred = m.train(dataX, dataY)
    print('Epoch:%04d' %(epoch+1),'cost:%.9f' % c)
    if epoch % 500 == 0:
        # predict the words using the softmax value
        for j,batch in enumerate(np.argmax(np.array(pred),axis=2).T):
            words = ' '.join([id2word[i] for i in batch])
            print(epoch,j,words)

print('Learning Finished')

Learning Started
Epoch:0001 cost:5.705245495
0 0 trained many-layered workshop when working involved published human learning object restricted 2006 workshop published working object et markov an hardware asr first involved from layers workshop started many dnns markov feature demonstrated from dnns asr neural involved asr published including nets trained asr up involved speech success from days cluttered lstm when asr speech object learning more dnns many dnns trained asr layers involved when which markov use involved speed involved from started algorithm time markov late called with an many into features automatic computer were demonstrated technology units when al involved learned brain technology asr boolean hardware neural survey it features working involved cascade belief systems trained published asr data workshop object how trained when days cascade evaluation used 1990s published . nets published system used could treating microsoft are published including lstm from hardware n

Epoch:0045 cost:4.545733929
Epoch:0046 cost:4.524764061
Epoch:0047 cost:4.534673214
Epoch:0048 cost:4.515880585
Epoch:0049 cost:4.524463177
Epoch:0050 cost:4.507543087
Epoch:0051 cost:4.515010357
Epoch:0052 cost:4.499700069
Epoch:0053 cost:4.506233692
Epoch:0054 cost:4.492307186
Epoch:0055 cost:4.498057842
Epoch:0056 cost:4.485322952
Epoch:0057 cost:4.490418434
Epoch:0058 cost:4.478710175
Epoch:0059 cost:4.483255863
Epoch:0060 cost:4.472435474
Epoch:0061 cost:4.476521015
Epoch:0062 cost:4.466467857
Epoch:0063 cost:4.470166206
Epoch:0064 cost:4.460779667
Epoch:0065 cost:4.464152813
Epoch:0066 cost:4.455345631
Epoch:0067 cost:4.458445549
Epoch:0068 cost:4.450143337
Epoch:0069 cost:4.453012943
Epoch:0070 cost:4.445151806
Epoch:0071 cost:4.447826385
Epoch:0072 cost:4.440352440
Epoch:0073 cost:4.442863464
Epoch:0074 cost:4.435729027
Epoch:0075 cost:4.438101768
Epoch:0076 cost:4.431265831
Epoch:0077 cost:4.433522224
Epoch:0078 cost:4.426950455
Epoch:0079 cost:4.429108620
Epoch:0080 cost:4.42

Epoch:0352 cost:3.903767109
Epoch:0353 cost:3.899597645
Epoch:0354 cost:3.900386572
Epoch:0355 cost:3.895875931
Epoch:0356 cost:3.899797916
Epoch:0357 cost:3.895623922
Epoch:0358 cost:3.903619289
Epoch:0359 cost:3.899020672
Epoch:0360 cost:3.905943155
Epoch:0361 cost:3.895386696
Epoch:0362 cost:3.894513607
Epoch:0363 cost:3.882161140
Epoch:0364 cost:3.878756523
Epoch:0365 cost:3.871078730
Epoch:0366 cost:3.869173765
Epoch:0367 cost:3.864597797
Epoch:0368 cost:3.864876032
Epoch:0369 cost:3.862619638
Epoch:0370 cost:3.864145994
Epoch:0371 cost:3.863539696
Epoch:0372 cost:3.860914469
Epoch:0373 cost:3.858219624
Epoch:0374 cost:3.851793051
Epoch:0375 cost:3.847300529
Epoch:0376 cost:3.842168808
Epoch:0377 cost:3.837929726
Epoch:0378 cost:3.833999634
Epoch:0379 cost:3.830236912
Epoch:0380 cost:3.826939344
Epoch:0381 cost:3.823506594
Epoch:0382 cost:3.820564747
Epoch:0383 cost:3.817335606
Epoch:0384 cost:3.814640522
Epoch:0385 cost:3.811532497
Epoch:0386 cost:3.809071541
Epoch:0387 cost:3.80

Epoch:0504 cost:3.498409271
Epoch:0505 cost:3.500524998
Epoch:0506 cost:3.492587805
Epoch:0507 cost:3.494936943
Epoch:0508 cost:3.487271309
Epoch:0509 cost:3.491282701
Epoch:0510 cost:3.484584093
Epoch:0511 cost:3.493243694
Epoch:0512 cost:3.487064600
Epoch:0513 cost:3.501973391
Epoch:0514 cost:3.486371517
Epoch:0515 cost:3.495629072
Epoch:0516 cost:3.471412420
Epoch:0517 cost:3.470596552
Epoch:0518 cost:3.457087517
Epoch:0519 cost:3.454735994
Epoch:0520 cost:3.448099375
Epoch:0521 cost:3.447286606
Epoch:0522 cost:3.444337130
Epoch:0523 cost:3.448207140
Epoch:0524 cost:3.448481798
Epoch:0525 cost:3.458227396
Epoch:0526 cost:3.453627348
Epoch:0527 cost:3.457239866
Epoch:0528 cost:3.444468975
Epoch:0529 cost:3.444198132
Epoch:0530 cost:3.437340498
Epoch:0531 cost:3.439374208
Epoch:0532 cost:3.443384647
Epoch:0533 cost:3.437888622
Epoch:0534 cost:3.442205191
Epoch:0535 cost:3.430130482
Epoch:0536 cost:3.423115015
Epoch:0537 cost:3.423370361
Epoch:0538 cost:3.411566973
Epoch:0539 cost:3.41

Epoch:0811 cost:2.695493937
Epoch:0812 cost:2.687269449
Epoch:0813 cost:2.686624050
Epoch:0814 cost:2.675179958
Epoch:0815 cost:2.668927193
Epoch:0816 cost:2.660981178
Epoch:0817 cost:2.655506849
Epoch:0818 cost:2.652102947
Epoch:0819 cost:2.648355246
Epoch:0820 cost:2.650531292
Epoch:0821 cost:2.647840261
Epoch:0822 cost:2.656510115
Epoch:0823 cost:2.652765989
Epoch:0824 cost:2.660591364
Epoch:0825 cost:2.652984619
Epoch:0826 cost:2.653872728
Epoch:0827 cost:2.645286798
Epoch:0828 cost:2.649431705
Epoch:0829 cost:2.641289473
Epoch:0830 cost:2.648747921
Epoch:0831 cost:2.637019634
Epoch:0832 cost:2.640286684
Epoch:0833 cost:2.627586365
Epoch:0834 cost:2.629102707
Epoch:0835 cost:2.619590521
Epoch:0836 cost:2.621844769
Epoch:0837 cost:2.613903046
Epoch:0838 cost:2.616710424
Epoch:0839 cost:2.607587576
Epoch:0840 cost:2.609284401
Epoch:0841 cost:2.599366903
Epoch:0842 cost:2.599375010
Epoch:0843 cost:2.590962648
Epoch:0844 cost:2.590358019
Epoch:0845 cost:2.584249258
Epoch:0846 cost:2.58

...

Epoch:2010 cost:1.167772770
Epoch:2011 cost:1.166102767
Epoch:2012 cost:1.166194558
Epoch:2013 cost:1.164573669
Epoch:2014 cost:1.164709568
Epoch:2015 cost:1.163158178
Epoch:2016 cost:1.163439035
Epoch:2017 cost:1.161964059
Epoch:2018 cost:1.162488222
Epoch:2019 cost:1.161079526
Epoch:2020 cost:1.161936522
Epoch:2021 cost:1.160564899
Epoch:2022 cost:1.161824465
Epoch:2023 cost:1.160439491
Epoch:2024 cost:1.162121058
Epoch:2025 cost:1.160651684
Epoch:2026 cost:1.162683129
Epoch:2027 cost:1.161047220
Epoch:2028 cost:1.163243651
Epoch:2029 cost:1.161376595
Epoch:2030 cost:1.163478732
Epoch:2031 cost:1.161365867
Epoch:2032 cost:1.163134813
Epoch:2033 cost:1.160823464
Epoch:2034 cost:1.162131310
Epoch:2035 cost:1.159716249
Epoch:2036 cost:1.160572052
Epoch:2037 cost:1.158165932
Epoch:2038 cost:1.158673763
Epoch:2039 cost:1.156376481
Epoch:2040 cost:1.156669497
Epoch:2041 cost:1.154546618
Epoch:2042 cost:1.154739976
Epoch:2043 cost:1.152816415
Epoch:2044 cost:1.152991056
Epoch:2045 cost:1.15

Epoch:2308 cost:1.060599566
Epoch:2309 cost:1.059292197
Epoch:2310 cost:1.059695482
Epoch:2311 cost:1.058456421
Epoch:2312 cost:1.058908343
Epoch:2313 cost:1.057716727
Epoch:2314 cost:1.058225989
Epoch:2315 cost:1.057061195
Epoch:2316 cost:1.057632923
Epoch:2317 cost:1.056475639
Epoch:2318 cost:1.057111621
Epoch:2319 cost:1.055945396
Epoch:2320 cost:1.056644917
Epoch:2321 cost:1.055455565
Epoch:2322 cost:1.056215525
Epoch:2323 cost:1.054993033
Epoch:2324 cost:1.055807829
Epoch:2325 cost:1.054545283
Epoch:2326 cost:1.055407047
Epoch:2327 cost:1.054101825
Epoch:2328 cost:1.055001497
Epoch:2329 cost:1.053654194
Epoch:2330 cost:1.054581404
Epoch:2331 cost:1.053195000
Epoch:2332 cost:1.054139256
Epoch:2333 cost:1.052719474
Epoch:2334 cost:1.053670049
Epoch:2335 cost:1.052223563
Epoch:2336 cost:1.053171158
Epoch:2337 cost:1.051704764
Epoch:2338 cost:1.052641034
Epoch:2339 cost:1.051161647
Epoch:2340 cost:1.052080393
Epoch:2341 cost:1.050594211
Epoch:2342 cost:1.051490903
Epoch:2343 cost:1.05

2500 1 for learning cresceptron model taken 's according gpus 2006 module later vanishing learned according boolean module while processing started since colleagues rnns 's hochreiter speech learned et 1990s 2009 speaker neural speech 2-d since processing speech , processing pre-trained colleagues colleagues , processing speech 's features restricted hochreiter speech human when that 2009 ( module started but success 1990s temporal , recognition taken 's model us layer boltzmann 's from 's hochreiter computer later 2009 processing called graphics first google 1990s layer 1990s training data systems speech pre-training published model other 's et its network colleagues was evaluation et technology times learning speech 's success 1990s with for according 2009 learning learned module 1990s involved model into but microsoft involved when combined network colleagues pre-trained into boltzmann speech since evaluation gradient according features network times according et 's data 's vanishin

Epoch:2552 cost:0.996139228
Epoch:2553 cost:0.995068431
Epoch:2554 cost:0.995632350
Epoch:2555 cost:0.994570732
Epoch:2556 cost:0.995123029
Epoch:2557 cost:0.994069517
Epoch:2558 cost:0.994612694
Epoch:2559 cost:0.993566155
Epoch:2560 cost:0.994103312
Epoch:2561 cost:0.993062019
Epoch:2562 cost:0.993596733
Epoch:2563 cost:0.992559135
Epoch:2564 cost:0.993095458
Epoch:2565 cost:0.992059529
Epoch:2566 cost:0.992601991
Epoch:2567 cost:0.991565645
Epoch:2568 cost:0.992119014
Epoch:2569 cost:0.991080165
Epoch:2570 cost:0.991649866
Epoch:2571 cost:0.990606368
Epoch:2572 cost:0.991198003
Epoch:2573 cost:0.990147829
Epoch:2574 cost:0.990766883
Epoch:2575 cost:0.989708364
Epoch:2576 cost:0.990359843
Epoch:2577 cost:0.989292026
Epoch:2578 cost:0.989979148
Epoch:2579 cost:0.988901913
Epoch:2580 cost:0.989625096
Epoch:2581 cost:0.988538802
Epoch:2582 cost:0.989294529
Epoch:2583 cost:0.988200009
Epoch:2584 cost:0.988979816
Epoch:2585 cost:0.987877011
Epoch:2586 cost:0.988668740
Epoch:2587 cost:0.98

Epoch:2849 cost:0.933732390
Epoch:2850 cost:0.934187174
Epoch:2851 cost:0.933363259
Epoch:2852 cost:0.933829784
Epoch:2853 cost:0.933001339
Epoch:2854 cost:0.933482230
Epoch:2855 cost:0.932648003
Epoch:2856 cost:0.933145463
Epoch:2857 cost:0.932304740
Epoch:2858 cost:0.932820499
Epoch:2859 cost:0.931972623
Epoch:2860 cost:0.932507575
Epoch:2861 cost:0.931652665
Epoch:2862 cost:0.932205617
Epoch:2863 cost:0.931344390
Epoch:2864 cost:0.931912541
Epoch:2865 cost:0.931045771
Epoch:2866 cost:0.931623995
Epoch:2867 cost:0.930752456
Epoch:2868 cost:0.931334198
Epoch:2869 cost:0.930458188
Epoch:2870 cost:0.931036770
Epoch:2871 cost:0.930155754
Epoch:2872 cost:0.930725574
Epoch:2873 cost:0.929838955
Epoch:2874 cost:0.930396140
Epoch:2875 cost:0.929503620
Epoch:2876 cost:0.930047035
Epoch:2877 cost:0.929148734
Epoch:2878 cost:0.929679334
Epoch:2879 cost:0.928776443
Epoch:2880 cost:0.929296494
Epoch:2881 cost:0.928390563
Epoch:2882 cost:0.928903401
Epoch:2883 cost:0.927996695
Epoch:2884 cost:0.92